In [ ]:
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim
from shapely.geometry import Point
from shapely.geometry import LineString
from shapely.geometry.polygon import Polygon
import shapefile as shp

In [ ]:
# for shapely library
!pip install pyshp

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
# merged data of charging stations with amenities within 100 m
final = pd.read_csv('datasets_out/comb.csv')
final

Unnamed: 0   latitude  longitude  college  food_court  hospital  \
0              0  51.497528  -0.127409      0.0         0.0       0.0   
1              1  51.497528  -0.127409      0.0         0.0       0.0   
2              2  51.499846  -0.160826      0.0         0.0       0.0   
3              3  51.499846  -0.160826      0.0         0.0       0.0   
4              4  51.499846  -0.160826      0.0         0.0       0.0   
...          ...        ...        ...      ...         ...       ...   
2201        2201  51.518793  -0.208326      0.0         0.0       0.0   
2202        2202  51.518793  -0.208326      0.0         0.0       0.0   
2203        2203  51.523651  -0.187735      0.0         0.0       0.0   
2204        2204  51.597523  -0.394100      0.0         0.0       0.0   
2205        2205  51.671658   0.102741      0.0         0.0       0.0   

      parking  restaurant  university   distance  charging_station  cs_idx  \
0         1.0         0.0         0.0  79.960982               1.0     5.0   
1         0.0         1.0         0.0  96.708749               1.0     5.0   
2         0.0         1.0         0.0  84.197376               1.0     6.0   
3         0.0         1.0         0.0  28.678070               1.0     6.0   
4         0.0         1.0         0.0  70.941383               1.0     6.0   
...       ...         ...         ...        ...               ...     ...   
2201      0.0         1.0         0.0  68.130566               1.0  3660.0   
2202      0.0         1.0         0.0  71.052101               1.0  3660.0   
2203      0.0         1.0         0.0  81.875520               1.0  3663.0   
2204      0.0         1.0         0.0  72.057304               1.0  3723.0   
2205      0.0         1.0         0.0  32.504631               1.0  3729.0   

      amenity_idx  
0          1491.0  
1          2027.0  
2          4862.0  
3          4863.0  
4          4864.0  
...           ...  
2201       4569.0  
2202       4570.0  
2203       4296.0  
2204       1396.0  
2205       1507.0  

[2206 rows x 13 columns]

In [ ]:
# nndexes of charging stations with amenity within 100 metres of them
cs_idx = final['cs_idx'].tolist()
cs_idx = list(set(cs_idx))
cs_idx = [int(id) for id in cs_idx]


In [ ]:
# indexes of amenity with charging station within 100 metres of them
amenity_idx = final['amenity_idx'].tolist()
amenity_idx = list(set(amenity_idx))
amenity_idx = [int(id) for id in amenity_idx]

In [ ]:
final.replace(0, np.nan, inplace=True)

In [ ]:
# combining duplicate entires based on latitude and longitude
final = final.groupby(["latitude", "longitude"])["college", "food_court", "hospital", "parking", "restaurant", "university", "charging_station"].sum().reset_index()

cols = ["college", "food_court", "hospital", "parking", "restaurant", "university", "charging_station"]

for col in cols:
  final[col].values[final[col] >= 1] = 1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  


In [ ]:
final

latitude  longitude  college  food_court  hospital  parking  restaurant  \
0    51.296097  -0.328327      0.0         0.0       0.0      0.0         1.0   
1    51.309677  -0.299971      0.0         0.0       0.0      0.0         1.0   
2    51.319156  -0.140250      0.0         0.0       0.0      0.0         1.0   
3    51.324567  -0.273913      0.0         0.0       0.0      0.0         1.0   
4    51.325722  -0.100303      0.0         0.0       0.0      0.0         1.0   
..         ...        ...      ...         ...       ...      ...         ...   
799  51.657030  -0.417732      0.0         0.0       0.0      1.0         0.0   
800  51.657402  -0.400939      0.0         0.0       0.0      0.0         1.0   
801  51.660202  -0.401118      0.0         0.0       0.0      1.0         1.0   
802  51.660640  -0.404182      0.0         0.0       0.0      1.0         0.0   
803  51.671658   0.102741      0.0         0.0       0.0      0.0         1.0   

     university  charging_station  
0           0.0               1.0  
1           0.0               1.0  
2           0.0               1.0  
3           0.0               1.0  
4           0.0               1.0  
..          ...               ...  
799         0.0               1.0  
800         0.0               1.0  
801         0.0               1.0  
802         0.0               1.0  
803         0.0               1.0  

[804 rows x 9 columns]

In [ ]:
cs_data = pd.read_csv('datasets_out/london_cs_data.csv')
cs_data

Unnamed: 0                                        AddressInfo  \
0            503  {'ID': 4133, 'Title': 'Glyn Hopkin Nissan', 'A...   
1            547  {'ID': 4359, 'Title': 'Masterpark Pimlico Car ...   
2            548  {'ID': 4363, 'Title': 'Vincent Square', 'Addre...   
3            549  {'ID': 4364, 'Title': 'Francis Street', 'Addre...   
4            550  {'ID': 4367, 'Title': 'NCP Cadogan Place', 'Ad...   
...          ...                                                ...   
3728      131869  {'ID': 188185, 'Title': 'Orphanage Road', 'Add...   
3729      131870  {'ID': 188186, 'Title': 'Theydon Bois', 'Addre...   
3730      132255  {'ID': 188571, 'Title': 'Premier Inn London En...   
3731      132256  {'ID': 188572, 'Title': 'Premier Inn London En...   
3732      132259  {'ID': 188575, 'Title': 'Premier Inn London En...   

                                           OperatorInfo   latitude  longitude  
0     {'ID': 7, 'Title': 'Nissan UK Dealer Network',...  51.682561   0.001116  
1     {'ID': 1, 'Title': '(Unknown Operator)', 'Webs...  51.488485  -0.143428  
2     {'ID': 1, 'Title': '(Unknown Operator)', 'Webs...  51.493841  -0.134172  
3     {'ID': 32, 'Title': 'BP Pulse', 'WebsiteURL': ...  51.495886  -0.137344  
4     {'ID': 32, 'Title': 'BP Pulse', 'WebsiteURL': ...  51.496370  -0.157076  
...                                                 ...        ...        ...  
3728  {'ID': 8, 'Title': 'Chargemaster', 'WebsiteURL...  51.661476  -0.391724  
3729  {'ID': 8, 'Title': 'Chargemaster', 'WebsiteURL...  51.671658   0.102741  
3730  {'ID': 150, 'Title': 'The GeniePoint Network (...  51.675332  -0.019660  
3731  {'ID': 150, 'Title': 'The GeniePoint Network (...  51.675709  -0.020354  
3732  {'ID': 150, 'Title': 'The GeniePoint Network (...  51.675332  -0.019660  

[3733 rows x 5 columns]

In [ ]:
# adding entries of charging stations with no amenities within 100 m

for index, cs in cs_data.iterrows():
    if index not in cs_idx:
      new_entry = {
            'latitude' : cs['latitude'],
            'longitude' : cs['longitude'],
            'college' : 0,
            'food_court': 0,
            'hospital' : 0,
            'parking' : 0,
            'restaurant' : 0,
            'university' : 0,
            'charging_station': 1
        }
        
      final = final.append(new_entry, ignore_index=True)


In [ ]:
amenities_data = pd.read_csv('datasets_out/only_amenities.csv')
amenities_data

Unnamed: 0 element_type        osmid                       name  \
0              0         node       451153         Central Restaurant   
1              1         node     12185812  Heston Services Eastbound   
2              2         node     13893285                        NaN   
3              3         node     13893291                        NaN   
4              4         node     17345465                        NaN   
...          ...          ...          ...                        ...   
5980        5980         node  10100610124                        NaN   
5981        5981         node  10101213926                    Nando's   
5982        5982         node  10105926114                     Taksim   
5983        5983         node  10111612429                Haute Dolci   
5984        5984         node  10111778732                    Hattusa   

                           geometry  college  food_court  hospital  parking  \
0     POINT (-0.1935029 51.6020306)        0           0         0        0   
1     POINT (-0.3884515 51.4888225)        0           0         0        1   
2     POINT (-0.0391511 51.4249457)        0           0         0        1   
3     POINT (-0.0386701 51.4253916)        0           0         0        1   
4     POINT (-0.0644718 51.6518261)        0           0         0        1   
...                             ...      ...         ...       ...      ...   
5980   POINT (0.0664892 51.4887177)        0           0         0        1   
5981  POINT (-0.1137773 51.3563644)        0           0         0        0   
5982  POINT (-0.0147866 51.4731125)        0           0         0        0   
5983  POINT (-0.3391611 51.5813745)        0           0         0        0   
5984   POINT (0.1836243 51.2769944)        0           0         0        0   

      restaurant  university   latitude  longitude  
0              1           0  51.602031  -0.193503  
1              0           0  51.488822  -0.388452  
2              0           0  51.424946  -0.039151  
3              0           0  51.425392  -0.038670  
4              0           0  51.651826  -0.064472  
...          ...         ...        ...        ...  
5980           0           0  51.488718   0.066489  
5981           1           0  51.356364  -0.113777  
5982           1           0  51.473112  -0.014787  
5983           1           0  51.581375  -0.339161  
5984           1           0  51.276994   0.183624  

[5985 rows x 13 columns]

In [ ]:
# adding entries of amenities with no charging station within 100 m
for index, am in amenities_data.iterrows():
    if index not in amenity_idx:
      new_entry = {
            'latitude' : am['latitude'],
            'longitude' : am['longitude'],
            'college' : am['college'],
            'food_court': am['food_court'],
            'hospital' : am['hospital'],
            'parking' : am['parking'],
            'restaurant' : am['restaurant'],
            'university' : am['university'],
            'charging_station': 0
        }
        
      final = final.append(new_entry, ignore_index=True)


In [ ]:
final = final.sample(frac=1, random_state=1)
final

latitude  longitude  college  food_court  hospital  parking  \
6087  51.510359  -0.187704      0.0         0.0       0.0      0.0   
7110  51.403444  -0.255276      0.0         0.0       0.0      1.0   
130   51.465290  -0.058371      0.0         0.0       0.0      0.0   
3792  51.438312  -0.156274      0.0         0.0       0.0      0.0   
4444  51.358167  -0.216632      0.0         0.0       0.0      0.0   
...         ...        ...      ...         ...       ...      ...   
7935  51.524390  -0.074412      0.0         0.0       0.0      0.0   
5192  51.588687   0.081108      0.0         0.0       0.0      0.0   
3980  51.561967  -0.074478      0.0         0.0       0.0      0.0   
235   51.492018  -0.156237      0.0         0.0       0.0      1.0   
5157  51.467770  -0.061842      0.0         0.0       0.0      0.0   

      restaurant  university  charging_station  
6087         1.0         0.0               0.0  
7110         0.0         0.0               0.0  
130          1.0         0.0               1.0  
3792         1.0         0.0               0.0  
4444         1.0         0.0               0.0  
...          ...         ...               ...  
7935         1.0         0.0               0.0  
5192         1.0         0.0               0.0  
3980         1.0         0.0               0.0  
235          1.0         0.0               1.0  
5157         1.0         0.0               0.0  

[8066 rows x 9 columns]

In [ ]:
final.to_csv('datasets_out/final_ev.csv')

In [ ]:
import folium
import tqdm


this_map = folium.Map(prefer_canvas=True)

def plotDotCS(latitude,longitude,color, this_map):
  
    folium.CircleMarker(location=[latitude, longitude],
                        radius=0.5,
                        weight=5,
                        color=color).add_to(this_map)



for latitude, longitude in zip(final['latitude'], final['longitude']):
  plotDotCS(latitude, longitude, 'blue', this_map)
   


this_map.fit_bounds(this_map.get_bounds())


this_map

In [ ]:
map